In [1]:
from pandas import *

from bokeh.plotting import figure
from bokeh.tile_providers import get_provider, CARTODBPOSITRON
from bokeh.io import output_notebook, show
from bokeh.models import LogColorMapper, ColumnDataSource
from bokeh.palettes import Oranges256 as oranges

from pyproj import Proj, transform

from sparql_dataframe import get
endpoint = 'https://dati.cultura.gov.it/sparql'

In [12]:
query = '''
SELECT DISTINCT(?CP) ?CPLabel ?institute ?instituteLabel ?lat ?long WHERE {
?CP a ?o.
FILTER (?o = arco:CulturalProperty || ?o = arco:IntangibleCulturalProperty || ?o = arco:TangibleCulturalProperty || ?o = arco:ArchaeologicalProperty || ?o = arco:ImmovableCulturalProperty || ?o = arco:ArchitecturalOrLandscapeHeritage || ?o = arco:HistoricOrArtisticProperty || ?o = arco:MusicHeritage || ?o = arco:NaturalHeritage || ?o = arco:BotanicalHeritage || ?o = arco:MineralHeritage || ?o = arco:PalaeontologicalHeritage || ?o = arco:PertologicHeritage || ?o = arco:PlanetaryScienceHeritage || ?o = arco:ZoologicalHeritage || ?o = arco:NumismaticProperty || ?o = arco:PhotographicHeritage || ?o = arco:ScientificOrTechnologicalHeritage)
?CP rdfs:label ?CPLabel;
a-loc:hasCulturalInstituteOrSite ?institute.
?institute rdfs:label ?instituteLabel.
  ?CP clvapit:hasGeometry ?geometry .
  ?geometry a-loc:hasCoordinates ?coordinates .
?coordinates a-loc:lat ?lat.
?coordinates a-loc:long ?long.
}
'''
CP_coordinates = get(endpoint, query)

In [13]:
CP_coordinates

CP  \
0      https://w3id.org/arco/resource/HistoricOrArtis...   
1      https://w3id.org/arco/resource/HistoricOrArtis...   
2      https://w3id.org/arco/resource/HistoricOrArtis...   
3      https://w3id.org/arco/resource/HistoricOrArtis...   
4      https://w3id.org/arco/resource/HistoricOrArtis...   
...                                                  ...   
29995  https://w3id.org/arco/resource/HistoricOrArtis...   
29996  https://w3id.org/arco/resource/HistoricOrArtis...   
29997  https://w3id.org/arco/resource/HistoricOrArtis...   
29998  https://w3id.org/arco/resource/HistoricOrArtis...   
29999  https://w3id.org/arco/resource/HistoricOrArtis...   

                                                 CPLabel  \
0           fiori (stampa) by Didier Euphèmie (sec. XIX)   
1           fiori (stampa) di Didier Euphèmie (sec. XIX)   
2      veduta di Napoli (stampa) di Daudet Robert (fi...   
3      veduta di Napoli (stampa) by Daudet Robert (fi...   
4      altare by Niccolini Antonio (prima metà sec. XIX)   
...                                                  ...   
29995  balza - manifattura fiamminga (secondo quarto ...   
29996  balza - manifattura di Alençon (primo quarto s...   
29997  balza - manifattura di Alençon (primo quarto s...   
29998  balza - manifattura di Alençon (primo quarto s...   
29999  balza - manifattura di Alençon (primo quarto s...   

                                               institute  \
0      https://w3id.org/arco/resource/CulturalInstitu...   
1      https://w3id.org/arco/resource/CulturalInstitu...   
2      https://w3id.org/arco/resource/CulturalInstitu...   
3      https://w3id.org/arco/resource/CulturalInstitu...   
4      https://w3id.org/arco/resource/CulturalInstitu...   
...                                                  ...   
29995  https://w3id.org/arco/resource/CulturalInstitu...   
29996  https://w3id.org/arco/resource/CulturalInstitu...   
29997  https://w3id.org/arco/resource/CulturalInstitu...   
29998  https://w3id.org/arco/resource/CulturalInstitu...   
29999  https://w3id.org/arco/resource/CulturalInstitu...   

                      instituteLabel        lat       long  
0                  Museo Tecnologico  43.776850  11.264717  
1                  Museo Tecnologico  43.776850  11.264717  
2                  Museo Tecnologico  43.776850  11.264717  
3                  Museo Tecnologico  43.776850  11.264717  
4      Museo della Reggia di Caserta  41.072296  14.327013  
...                              ...        ...        ...  
29995     Museo di Palazzo Davanzati  43.770209  11.253101  
29996     Museo di Palazzo Davanzati  43.770209  11.253101  
29997     Museo di Palazzo Davanzati  43.770209  11.253101  
29998     Museo di Palazzo Davanzati  43.770209  11.253101  
29999     Museo di Palazzo Davanzati  43.770209  11.253101  

[30000 rows x 6 columns]

In [17]:
#since I have the institute for the properties I should keep the site instead of the subject
query = '''
SELECT DISTINCT(?s) ?event ?dbpedia ?label WHERE {
 ?s a cis:CulturalEvent;
rdfs:label ?event.
?s cis:isHostedBySite ?o.
?o rdfs:label ?site.
?o cis:siteAddress ?address.
?address clvapit:hasCity ?urlcity.
?urlcity owl:sameAs ?urlcity2.
?urlcity2 rdfs:label ?label.
?urlcity2 owl:sameAs ?dbpedia.
FILTER (contains(str(?dbpedia), "dbpedia"))
}
'''

dbPediaLinks = get(endpoint, query)
dbPediaLinks

s  \
0      http://dati.beniculturali.it/mibact/eventi/res...   
1      http://dati.beniculturali.it/mibact/eventi/res...   
2      http://dati.beniculturali.it/mibact/eventi/res...   
3      http://dati.beniculturali.it/mibact/eventi/res...   
4      http://dati.beniculturali.it/mibact/eventi/res...   
...                                                  ...   
21959  http://dati.beniculturali.it/mibact/eventi/res...   
21960  http://dati.beniculturali.it/mibact/eventi/res...   
21961  http://dati.beniculturali.it/mibact/eventi/res...   
21962  http://dati.beniculturali.it/mibact/eventi/res...   
21963  http://dati.beniculturali.it/mibact/eventi/res...   

                                                   event  \
0      Palazzo Mediceo: il patrimonio De’Medici in Ve...   
1           Orvieto – Area archeologica della Cannicella   
2      Collemancio di Cannara – Area archeologica di ...   
3                      AQUANAE Performance site specific   
4                                            ASSISI 1822   
...                                                  ...   
21959  Geronimo Stilton in Biblioteca Vallicelliana -...   
21960  MIRABILIA 2. CAPOLAVORI A CONFRONTO. Gli orecc...   
21961  Apertura straordinaria di Palazzo Patrizi Clem...   
21962   Apertura straordinaria del Mitreo di Marino (RM)   
21963                        Voci diverse, dolci melodie   

                                         dbpedia      label  
0          http://dbpedia.org/resource/Seravezza  Seravezza  
1            http://dbpedia.org/resource/Orvieto    Orvieto  
2            http://dbpedia.org/resource/Cannara    Cannara  
3              http://dbpedia.org/resource/Lucca      Lucca  
4             http://dbpedia.org/resource/Assisi     Assisi  
...                                          ...        ...  
21959           http://dbpedia.org/resource/Rome       Roma  
21960       http://dbpedia.org/resource/Aquileia   Aquileia  
21961           http://dbpedia.org/resource/Rome       Roma  
21962  http://dbpedia.org/resource/Marino,_Lazio     Marino  
21963          http://dbpedia.org/resource/Sarno      Sarno  

[21964 rows x 4 columns]

In [19]:
dbpedia = dbPediaLinks["dbpedia"].drop_duplicates()
link = []

endpointDB = 'https://dbpedia.org/sparql'

CE_coordinates = DataFrame({"latitude":[], "longitude":[]})

for idx, item in dbpedia.items():
    query = '''
    SELECT ?latitude ?longitude WHERE {
       '''f'<{item}>''''  geo:lat ?latitude;
        geo:long ?longitude.
    } '''
    coordinates = get(endpointDB, query)
    link.append(item)
    CE_coordinates = concat([CE_coordinates, coordinates])

CE_coordinates.insert(0, "dbPedia", link)
CE_coordinates

In [17]:
print(CE_coordinates)

                                              dbPedia  latitude  longitude
0               http://dbpedia.org/resource/Besenello   45.9333   11.11670
0                   http://dbpedia.org/resource/Calci   43.7167   10.51670
0              http://dbpedia.org/resource/Carmignano   43.8167   11.01670
0                  http://dbpedia.org/resource/Cetona   42.9667   11.90000
0                  http://dbpedia.org/resource/Chiusi   43.0167   11.95000
..                                                ...       ...        ...
0            http://dbpedia.org/resource/Casalciprano   41.5833   14.53330
0        http://dbpedia.org/resource/Monterosso_Grana   44.4167    7.31667
0             http://dbpedia.org/resource/Castrocielo   41.5333   13.70000
0   http://dbpedia.org/resource/Lu_e_Cuccaro_Monfe...   44.9972    8.47222
0                  http://dbpedia.org/resource/Sinnai   39.3000    9.20000

[794 rows x 3 columns]


In [18]:
CE_coordinates_cleaned = CE_coordinates.merge(dbPediaLinks, left_on="dbPedia", right_on="dbpedia")
CE_coordinates_cleaned

dbPedia  latitude  longitude  \
0                  http://dbpedia.org/resource/Besenello   45.9333   11.11670   
1                      http://dbpedia.org/resource/Calci   43.7167   10.51670   
2                      http://dbpedia.org/resource/Calci   43.7167   10.51670   
3                      http://dbpedia.org/resource/Calci   43.7167   10.51670   
4                      http://dbpedia.org/resource/Calci   43.7167   10.51670   
...                                                  ...       ...        ...   
21959           http://dbpedia.org/resource/Casalciprano   41.5833   14.53330   
21960       http://dbpedia.org/resource/Monterosso_Grana   44.4167    7.31667   
21961            http://dbpedia.org/resource/Castrocielo   41.5333   13.70000   
21962  http://dbpedia.org/resource/Lu_e_Cuccaro_Monfe...   44.9972    8.47222   
21963                 http://dbpedia.org/resource/Sinnai   39.3000    9.20000   

                                                       s  \
0      http://dati.beniculturali.it/mibact/eventi/res...   
1      http://dati.beniculturali.it/mibact/eventi/res...   
2      http://dati.beniculturali.it/mibact/eventi/res...   
3      http://dati.beniculturali.it/mibact/eventi/res...   
4      http://dati.beniculturali.it/mibact/eventi/res...   
...                                                  ...   
21959  http://dati.beniculturali.it/mibact/eventi/res...   
21960  http://dati.beniculturali.it/mibact/eventi/res...   
21961  http://dati.beniculturali.it/mibact/eventi/res...   
21962  http://dati.beniculturali.it/mibact/eventi/res...   
21963  http://dati.beniculturali.it/mibact/eventi/res...   

                                                 dbpedia  
0                  http://dbpedia.org/resource/Besenello  
1                      http://dbpedia.org/resource/Calci  
2                      http://dbpedia.org/resource/Calci  
3                      http://dbpedia.org/resource/Calci  
4                      http://dbpedia.org/resource/Calci  
...                                                  ...  
21959           http://dbpedia.org/resource/Casalciprano  
21960       http://dbpedia.org/resource/Monterosso_Grana  
21961            http://dbpedia.org/resource/Castrocielo  
21962  http://dbpedia.org/resource/Lu_e_Cuccaro_Monfe...  
21963                 http://dbpedia.org/resource/Sinnai  

[21964 rows x 5 columns]

In [22]:
CE_coordinates_cleaned = CE_coordinates_cleaned[["event", "label", "latitude", "longitude"]].drop_duplicates(subset= ["s"])
CE_coordinates_cleaned.reset_index()

index                                                  s  latitude  \
0          0  http://dati.beniculturali.it/mibact/eventi/res...   45.9333   
1          1  http://dati.beniculturali.it/mibact/eventi/res...   43.7167   
2          2  http://dati.beniculturali.it/mibact/eventi/res...   43.7167   
3          3  http://dati.beniculturali.it/mibact/eventi/res...   43.7167   
4          4  http://dati.beniculturali.it/mibact/eventi/res...   43.7167   
...      ...                                                ...       ...   
20475  21958  http://dati.beniculturali.it/mibact/eventi/res...   44.5167   
20476  21959  http://dati.beniculturali.it/mibact/eventi/res...   41.5833   
20477  21960  http://dati.beniculturali.it/mibact/eventi/res...   44.4167   
20478  21962  http://dati.beniculturali.it/mibact/eventi/res...   44.9972   
20479  21963  http://dati.beniculturali.it/mibact/eventi/res...   39.3000   

       longitude  
0       11.11670  
1       10.51670  
2       10.51670  
3       10.51670  
4       10.51670  
...          ...  
20475    7.46667  
20476   14.53330  
20477    7.31667  
20478    8.47222  
20479    9.20000  

[20480 rows x 4 columns]

In [20]:
CP_coordinates.to_csv("CP_coordinates.csv")
CE_coordinates_cleaned.to_csv("CE_coordinates.csv")

In [14]:


# projection WGS 84 - used by GPS
inProj = Proj(init='epsg:4326')

# WGS84 Pseudo Web Mercator - projection used by most web services, e.g. Google Maps, OpenStreet Maps
outProj = Proj(init='epsg:3857')

CP_coordinates['long'],CP_coordinates['lat'] = transform(inProj,outProj,CP_coordinates['long'].values,CP_coordinates['lat'].values)
CP_coordinates.head()

c:\Users\bianc\AppData\Local\Programs\Python\Python310\lib\site-packages\pyproj\crs\crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
c:\Users\bianc\AppData\Local\Programs\Python\Python310\lib\site-packages\pyproj\crs\crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
C:\Users\bianc\AppData\Local\Temp\ipykernel_35896\3267530211.py:7: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotc

CP  \
0  https://w3id.org/arco/resource/HistoricOrArtis...   
1  https://w3id.org/arco/resource/HistoricOrArtis...   
2  https://w3id.org/arco/resource/HistoricOrArtis...   
3  https://w3id.org/arco/resource/HistoricOrArtis...   
4  https://w3id.org/arco/resource/HistoricOrArtis...   

                                             CPLabel  \
0       fiori (stampa) by Didier Euphèmie (sec. XIX)   
1       fiori (stampa) di Didier Euphèmie (sec. XIX)   
2  veduta di Napoli (stampa) di Daudet Robert (fi...   
3  veduta di Napoli (stampa) by Daudet Robert (fi...   
4  altare by Niccolini Antonio (prima metà sec. XIX)   

                                           institute  \
0  https://w3id.org/arco/resource/CulturalInstitu...   
1  https://w3id.org/arco/resource/CulturalInstitu...   
2  https://w3id.org/arco/resource/CulturalInstitu...   
3  https://w3id.org/arco/resource/CulturalInstitu...   
4  https://w3id.org/arco/resource/CulturalInstitu...   

                  instituteLabel           lat          long  
0              Museo Tecnologico  5.430974e+06  1.253983e+06  
1              Museo Tecnologico  5.430974e+06  1.253983e+06  
2              Museo Tecnologico  5.430974e+06  1.253983e+06  
3              Museo Tecnologico  5.430974e+06  1.253983e+06  
4  Museo della Reggia di Caserta  5.023011e+06  1.594876e+06

In [15]:
# create a dictionary with lists
source = ColumnDataSource(data=dict(
    lat=CP_coordinates.lat.values.tolist(),
    lon=CP_coordinates.long.values.tolist(),
    name=CP_coordinates.CPLabel.values.tolist(),
    keeper=CP_coordinates.instituteLabel.values.tolist()
))

In [16]:
# import tile
cartodb = get_provider(CARTODBPOSITRON)

# draw the frame
p = figure(outer_width=900, outer_height=700,
           x_range=(-2000000, 6000000), y_range=(-1000000, 7000000), # range EU/Africa
           x_axis_type="mercator", y_axis_type="mercator", # labels on axes
           tooltips=[ ("Name", "@name, @keeper")],
           title="Cultural Properties sites")

# add tile
p.add_tile(cartodb)

# draw points
p.circle(x='lon', y='lat',
         size=10,
         fill_color="dodgerblue", line_color="dodgerblue",
         fill_alpha=0.3,
         source=source)

# add for colab output
output_notebook()

show(p)

Loading BokehJS ...